In [ ]:
!pip install praw
!pip install requests

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 189.3/189.3 kB 3.8 MB/s eta 0:00:00


In [ ]:
import praw
import requests
import os
import csv
# NEW: Import the Google Drive library
from google.colab import drive

# --- NEW: MOUNT YOUR GOOGLE DRIVE ---
# This will prompt you for authorization when you run it.
print("Connecting to Google Drive...")
drive.mount('/content/drive')
print("Google Drive connected successfully!")


# --- CONFIGURATION ---
# Step 1: Your Reddit API credentials
CLIENT_ID = "GqCbGMNlJsb-uNWMoYJxxA"
CLIENT_SECRET = "nzTshKEW6zUj890WtdqXIHb3gu9psg"
USER_AGENT = "VibeProjectMemeScraper/0.3 by fat_candy"

# Step 2: Define your target subreddits
TARGET_SUBREDDITS = [
    "PoliticalMemes",
    "IndiaSpeaks",
    "IndianDankMemes",
    "DesiMeta",
    "IndianPoliticalMemes",
    "PoliticalHumor",
    "IndiaNews",
    "Indiasocial",
    "GenZedong"
]

# Step 3: Customize your scrape
SORT_METHOD = 'top'
TIME_FILTER = 'year'
POST_LIMIT = 100

# --- UPDATED: Define the paths to save files in your Google Drive ---
# The main folder will be created in your Google Drive's root directory.
DRIVE_FOLDER_PATH = "/content/drive/My Drive/reddit_political_memes"
DOWNLOAD_FOLDER = DRIVE_FOLDER_PATH
METADATA_FILE = os.path.join(DOWNLOAD_FOLDER, "metadata.csv")


# --- THE SCRIPT (No changes needed below this line) ---

def setup_praw():
    """Initializes and returns a PRAW Reddit instance."""
    print("Connecting to Reddit...")
    return praw.Reddit(client_id=CLIENT_ID, client_secret=CLIENT_SECRET, user_agent=USER_AGENT)

def setup_environment():
    """Creates download folder and sets up the CSV file with headers."""
    if not os.path.exists(DOWNLOAD_FOLDER):
        print(f"Creating Google Drive folder: '{DOWNLOAD_FOLDER}'")
        os.makedirs(DOWNLOAD_FOLDER)

    with open(METADATA_FILE, 'w', newline='', encoding='utf-8') as f:
        writer = csv.writer(f)
        writer.writerow(['subreddit', 'post_id', 'title', 'score', 'post_url', 'local_filename'])

def download_image(url, filepath):
    """Downloads an image from a URL and saves it."""
    try:
        response = requests.get(url, stream=True)
        if response.status_code == 200:
            with open(filepath, 'wb') as f:
                f.write(response.content)
            return True
    except requests.exceptions.RequestException as e:
        print(f"   !! Error downloading {url}: {e}")
    return False

def log_metadata(subreddit, post, local_filename):
    """Appends a row to the metadata CSV file."""
    # We strip the main drive path to keep the CSV cleaner
    relative_filename = local_filename.replace(DOWNLOAD_FOLDER + '/', '')
    with open(METADATA_FILE, 'a', newline='', encoding='utf-8') as f:
        writer = csv.writer(f)
        writer.writerow([subreddit, post.id, post.title, post.score, f"https://www.reddit.com{post.permalink}", relative_filename])

def scrape_subreddits(reddit):
    """Main function to loop through subreddits and download content."""
    print(f"\n--- Starting Scrape (Mode: {SORT_METHOD}, Limit: {POST_LIMIT}) ---")
    total_downloads = 0

    for sub_name in TARGET_SUBREDDITS:
        sub_folder = os.path.join(DOWNLOAD_FOLDER, sub_name)
        if not os.path.exists(sub_folder):
            os.makedirs(sub_folder)

        print(f"\n[+] Scraping subreddit: r/{sub_name}")
        try:
            subreddit = reddit.subreddit(sub_name)

            if SORT_METHOD == 'top':
                posts = subreddit.top(time_filter=TIME_FILTER, limit=POST_LIMIT)
            elif SORT_METHOD == 'hot':
                posts = subreddit.hot(limit=POST_LIMIT)
            elif SORT_METHOD == 'new':
                posts = subreddit.new(limit=POST_LIMIT)
            else:
                print(f"   !! Invalid SORT_METHOD: {SORT_METHOD}. Skipping subreddit.")
                continue

            sub_download_count = 0
            for post in posts:
                if hasattr(post, 'is_gallery') and post.is_gallery:
                    gallery_count = 0
                    for i, item in enumerate(post.media_metadata.items()):
                        image_url = item[1]['s']['u']
                        file_ext = image_url.split('?')[0].split('.')[-1]
                        filename = f"{sub_name}_{post.id}_{i+1}.{file_ext}"
                        filepath = os.path.join(sub_folder, filename)

                        if not os.path.exists(filepath):
                            if download_image(image_url, filepath):
                                gallery_count += 1
                                log_metadata(sub_name, post, filepath)
                    if gallery_count > 0:
                        print(f"   -> Downloaded {gallery_count} images from gallery: {post.title[:50]}...")
                        sub_download_count += gallery_count

                elif post.url.endswith(('.jpg', '.jpeg', '.png', '.gif')):
                    file_extension = os.path.splitext(post.url)[1]
                    filename = f"{sub_name}_{post.id}{file_extension}"
                    filepath = os.path.join(sub_folder, filename)

                    if not os.path.exists(filepath):
                        if download_image(post.url, filepath):
                            print(f"   -> Downloaded image: {filename}")
                            sub_download_count += 1
                            log_metadata(sub_name, post, filepath)

            print(f"[+] Downloaded {sub_download_count} new images from r/{sub_name}.")
            total_downloads += sub_download_count

        except Exception as e:
            print(f"   !! An error occurred with r/{sub_name}: {e}")

    print("\n--- Scrape Finished ---")
    print(f"Total new images downloaded: {total_downloads}")
    print(f"All files saved in your Google Drive at: '{DRIVE_FOLDER_PATH}'")


# --- Main Execution ---
if __name__ == "__main__":
    reddit_instance = setup_praw()
    setup_environment()
    scrape_subreddits(reddit_instance)

Connecting to Google Drive...


It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.



Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Google Drive connected successfully!
Connecting to Reddit...
Creating Google Drive folder: '/content/drive/My Drive/reddit_political_memes'

--- Starting Scrape (Mode: top, Limit: 100) ---

[+] Scraping subreddit: r/PoliticalMemes


It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.



   -> Downloaded image: PoliticalMemes_1heui3k.jpeg


...

   -> Downloaded image: Indiasocial_1o0i9f1.jpeg
   -> Downloaded image: Indiasocial_1ot9di8.png


It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.



   -> Downloaded 3 images from gallery: Guys look i made it💫...


It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.



   -> Downloaded image: Indiasocial_1nqb8u1.jpeg
[+] Downloaded 140 new images from r/Indiasocial.

[+] Scraping subreddit: r/GenZedong
   !! An error occurred with r/GenZedong: received 403 HTTP response

--- Scrape Finished ---
Total new images downloaded: 572
All files saved in your Google Drive at: '/content/drive/My Drive/reddit_political_memes'


In [ ]:
# Python packages
!pip install pillow pytesseract pandas langdetect vaderSentiment deep-translator nltk emoji matplotlib wordfreq gensim pyldavis scikit-learn transformers torch sentencepiece
# optional but recommended for better tokenization/lemmatization
!pip install nltk
!python -m nltk.downloader punkt stopwords wordnet


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 44.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 126.0/126.0 kB 10.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.3/42.3 kB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 608.4/608.4 kB 39.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.8/56.8 MB 17.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 27.9/27.9 MB 34.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 88.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.8/44.8 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 183.0/183.0 kB 15.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.4/5.4 MB 107.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 57.7 MB/s eta 0:00:00
  Created wheel for langdetect: filename=langdetect-1.0.9-py3-none-any.whl size=993223 sh

In [ ]:
# process_local_meme_images.py
import os, re, json
from pathlib import Path
from datetime import datetime
from PIL import Image
import pytesseract
import pandas as pd
from langdetect import detect, DetectorFactory
from deep_translator import GoogleTranslator
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
import matplotlib.pyplot as plt
import nltk
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer, WordNetLemmatizer
from nltk.tokenize import word_tokenize

# Make langdetect deterministic
DetectorFactory.seed = 0

# ---------- CONFIG ----------
# Set this to the parent folder that contains subreddit folders (example from your screenshot)
ROOT_DIR = "/content/drive/MyDrive/reddit_political_memes"   # <-- change this to your path
OUT_DIR = os.path.join(ROOT_DIR, "processed_results")
TESS_LANG = "eng+hin"   # install tesseract hin if you want better Devanagari OCR. Use 'eng' only if not installed.
# ----------------------------

pytesseract.pytesseract.tesseract_cmd = pytesseract.pytesseract.tesseract_cmd  # use default PATH

nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('punkt_tab') # Added to fix the LookupError

STOPWORDS = set(stopwords.words('english'))
PS = PorterStemmer()
LEMMA = WordNetLemmatizer()
VADER = SentimentIntensityAnalyzer()

os.makedirs(OUT_DIR, exist_ok=True)

def clean_text(s):
    s = (s or "").lower()
    s = re.sub(r'<.*?>', ' ', s)
    s = re.sub(r'http\S+|www\.\S+', ' ', s)
    try:
        # demojize if emoji lib installed
        from emoji import demojize
        s = demojize(s)
    except Exception:
        pass
    s = re.sub(r"[^a-zA-Z0-9\s\-\']", ' ', s)
    s = re.sub(r'\s+', ' ', s).strip()
    return s

def tokenize_normalize(s):
    toks = word_tokenize(s)
    toks = [t for t in toks if t not in STOPWORDS and len(t) > 1]
    toks = [PS.stem(t) for t in toks]
    toks = [LEMMA.lemmatize(t) for t in toks]
    return toks

def translate_text(s):
    if not s or s.strip() == "":
        return s
    try:
        return GoogleTranslator(source='auto', target='en').translate(s)
    except Exception:
        return s

def detect_lang_safe(s):
    try:
        return detect(s) if s and s.strip() else "unknown"
    except Exception:
        return "unknown"

rows = []
for subfolder in sorted(Path(ROOT_DIR).iterdir()):
    if not subfolder.is_dir():
        continue
    subreddit_name = subfolder.name
    print("Processing subreddit:", subreddit_name)
    for img_path in sorted(subfolder.glob("*")):
        if img_path.suffix.lower() not in {'.jpg', '.jpeg', '.png'}:
            continue
        try:
            # OCR
            text = pytesseract.image_to_string(Image.open(img_path), lang=TESS_LANG)
        except Exception as e:
            print("OCR fail:", img_path, e)
            text = ""

        # if you have metadata (timestamp, title) saved elsewhere, merge here.
        # For now we use filename as id and no timestamp.
        meta_title = img_path.stem

        combined = " ".join([meta_title, text])
        cleaned = clean_text(combined)
        tokens = tokenize_normalize(cleaned)
        joined = " ".join(tokens)

        lang = detect_lang_safe(joined)
        translated = joined
        if lang != 'en' and lang != 'unknown':
            translated = translate_text(joined)

        # VADER sentiment (english)
        vs = VADER.polarity_scores(translated)
        comp = vs['compound']
        if comp >= 0.05:
            sent_label = 'positive'
        elif comp <= -0.05:
            sent_label = 'negative'
        else:
            sent_label = 'neutral'

        rows.append({
            'id': str(img_path.name),
            'subreddit': subreddit_name,
            'filepath': str(img_path),
            'title_meta': meta_title,
            'ocr_text': text,
            'cleaned': cleaned,
            'tokens': tokens,
            'lang': lang,
            'translated': translated,
            'compound': comp,
            'sent_label': sent_label,
        })

# Save results
df = pd.DataFrame(rows)
csv_path = os.path.join(OUT_DIR, 'meme_sentiment_results.csv')
json_path = os.path.join(OUT_DIR, 'meme_sentiment_results.json')
df.to_csv(csv_path, index=False)
df.to_json(json_path, orient='records', force_ascii=False)
print("Saved:", csv_path, json_path)

# Plots
plt.figure(figsize=(6,4))
df['sent_label'].value_counts().reindex(['positive','neutral','negative']).plot(kind='bar')
plt.title('Sentiment distribution')
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR, 'sentiment_counts.png'))
plt.close()
print("Plots saved to", OUT_DIR)


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


Processing subreddit: DesiMeta
Processing subreddit: GenZedong
Processing subreddit: IndiaNews
Processing subreddit: IndiaSpeaks
Processing subreddit: IndianDankMemes
Processing subreddit: IndianPoliticalMemes
Processing subreddit: Indiasocial
Processing subreddit: PoliticalHumor
Processing subreddit: PoliticalMemes
Processing subreddit: processed_results
Saved: /content/drive/MyDrive/reddit_political_memes/processed_results/meme_sentiment_results.csv /content/drive/MyDrive/reddit_political_memes/processed_results/meme_sentiment_results.json
Plots saved to /content/drive/MyDrive/reddit_political_memes/processed_results


In [ ]:
import os
import pandas as pd
import matplotlib.pyplot as plt
from wordcloud import WordCloud
from collections import Counter
import nltk
from nltk.util import ngrams
import networkx as nx
import seaborn as sns

# Define ROOT_DIR and OUT_DIR as they are used to locate the CSV file
ROOT_DIR = "/content/drive/MyDrive/reddit_political_memes"
OUT_DIR = os.path.join(ROOT_DIR, "processed_results")

# Ensure OUT_DIR exists, though it should have been created by previous cells
os.makedirs(OUT_DIR, exist_ok=True)

# Load the DataFrame again from the CSV file
csv_file_path = os.path.join(OUT_DIR, "meme_sentiment_results.csv")
df = pd.read_csv(csv_file_path)

plt.figure(figsize=(7,5))
sns.countplot(data=df, x="sent_label",
              order=['positive','neutral','negative'],
              hue='sent_label', legend=False, # Added hue and legend=False to address FutureWArning
              palette="viridis")

plt.title("Sentiment Distribution of Political Memes (Jan–Jun 2024)", fontsize=14)
plt.xlabel("Sentiment")
plt.ylabel("Count")
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR, "sentiment_distribution.png"))
plt.close()


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
plt.figure(figsize=(10,6))
sns.countplot(data=df, x="subreddit", hue="sent_label",
              order=sorted(df['subreddit'].unique()), palette="viridis")

plt.xticks(rotation=45)
plt.title("Subreddit-wise Sentiment Comparison")
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR, "subreddit_sentiment.png"))
plt.close()


In [ ]:
from wordcloud import WordCloud

all_text = " ".join(df["cleaned"].astype(str))

wc = WordCloud(width=1000, height=600, background_color="white").generate(all_text)

plt.figure(figsize=(12,8))
plt.imshow(wc, interpolation='bilinear')
plt.axis("off")
plt.title("Wordcloud of Political Meme Text", fontsize=16)
plt.savefig(os.path.join(OUT_DIR, "wordcloud.png"))
plt.close()


In [ ]:
from collections import Counter

token_list = df["tokens"].explode().dropna().tolist()
counts = Counter(token_list)
common = pd.DataFrame(counts.most_common(20), columns=["token","freq"])

plt.figure(figsize=(10,6))
sns.barplot(data=common, x="freq", y="token", palette="viridis")
plt.title("Top 20 Most Frequent Tokens in Memes")
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR, "top_tokens.png"))
plt.close()


/tmp/ipython-input-3297276166.py:8: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.

  sns.barplot(data=common, x="freq", y="token", palette="viridis")
/tmp/ipython-input-3297276166.py:10: UserWarning: Tight layout not applied. The left and right margins cannot be made large enough to accommodate all Axes decorations.
  plt.tight_layout()


In [ ]:
plt.figure(figsize=(10,6))
sns.barplot(data=df, x="subreddit", y="compound",
            estimator="mean", palette="coolwarm")

plt.xticks(rotation=45)
plt.title("Average Sentiment Score per Subreddit")
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR, "avg_sentiment_subreddit.png"))
plt.close()


/tmp/ipython-input-128396144.py:2: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `x` variable to `hue` and set `legend=False` for the same effect.

  sns.barplot(data=df, x="subreddit", y="compound",


In [ ]:
df["text_len"] = df["ocr_text"].astype(str).apply(len)

plt.figure(figsize=(8,5))
sns.histplot(df["text_len"], kde=True, bins=40)
plt.title("Distribution of OCR Text Lengths")
plt.xlabel("Characters extracted")
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR, "ocr_text_length.png"))
plt.close()


In [ ]:
# -------------------- START: Topic Modeling + Sarcasm + Hate Detection --------------------

# Install note:
!pip install gensim pyldavis # Ensure gensim and pyLDAvis are installed in this environment

import warnings
warnings.filterwarnings('ignore')

from gensim import corpora, models
from gensim.parsing.preprocessing import preprocess_string, strip_punctuation, strip_numeric, remove_stopwords, strip_short
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
import json
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis
import os # Import os module
import pandas as pd # Import pandas to load the DataFrame

# Transformers for sarcasm/hate detection
from transformers import pipeline

# Define ROOT_DIR and OUT_DIR as they are needed for path construction
ROOT_DIR = "/content/drive/MyDrive/reddit_political_memes"
OUT_DIR = os.path.join(ROOT_DIR, "processed_results")
csv_path = os.path.join(OUT_DIR, 'meme_sentiment_results.csv')
json_path = os.path.join(OUT_DIR, 'meme_sentiment_results.json')

# Load the DataFrame
df = pd.read_csv(csv_path)

# Handle tokens column which might be read as string representation of list
def parse_tokens_from_string(s):
    try:
        return json.loads(s.replace("'", '"')) # Convert single quotes to double quotes for valid JSON
    except (json.JSONDecodeError, AttributeError):
        return []

df['tokens'] = df['tokens'].apply(parse_tokens_from_string)


# ---------- PREPROCESS TEXT FOR TOPIC MODELLING ----------
def gensim_preprocess(text):
    # reuse earlier clean_text/tokenize if desired; gensim preprocessing for LDA:
    custom_filters = [lambda x: x.lower(), strip_punctuation, strip_numeric, remove_stopwords, strip_short]
    return preprocess_string(text or "", custom_filters)

# create a tokens column if not present (it is present in your script)
# The above line is defensive but a little odd — simpler: if tokens present, join them, else run gensim_preprocess
# Let's correct more robustly:
def _ensure_tokens(row):
    if isinstance(row['tokens'], list) and len(row['tokens'])>0:
        return [w for w in row['tokens']]
    else:
        return gensim_preprocess(row['cleaned'] or "")
df['processed_for_topics'] = df.apply(_ensure_tokens, axis=1)

# Filter out empty documents
topic_docs = df['processed_for_topics'].apply(lambda x: x if x and len(x)>0 else None).dropna().tolist()

# create dictionary and corpus
dictionary = corpora.Dictionary(topic_docs)
# Filter extremes to remove very rare and very common tokens
dictionary.filter_extremes(no_below=3, no_above=0.5)  # tune these
corpus = [dictionary.doc2bow(doc) for doc in topic_docs]

if len(dictionary) == 0 or len(corpus) == 0:
    print("Not enough tokens for LDA. Skipping topic modelling.")
    df['dominant_topic'] = None
    df['topic_keywords'] = None
else:
    # ---------- LDA Model ----------
    NUM_TOPICS = 6  # tune (try 5-12)
    lda = models.LdaModel(corpus=corpus,
                          id2word=dictionary,
                          num_topics=NUM_TOPICS,
                          random_state=42,
                          passes=10,
                          alpha='auto',
                          per_word_topics=True)

    # map each doc in corpus back to row to assign dominant topic
    # build topic keywords
    topic_keywords = {}
    for tid in range(NUM_TOPICS):
        words_probs = lda.show_topic(tid, topn=8)
        topic_keywords[tid] = ", ".join([w for w,p in words_probs])

    # Get dominant topic per doc
    def get_doc_topic(bow):
        topics = lda.get_document_topics(bow)
        if not topics:
            return None, None
        topics = sorted(topics, key=lambda x: x[1], reverse=True)
        tid, score = topics[0]
        return int(tid), float(score)

    # Apply only to non-empty docs and then put back into df
    doc_topics = [get_doc_topic(b) for b in corpus]  # corresponds to topic_docs order
    # create a mapping from doc index in topic_docs -> df index
    # our topic_docs was built from df.dropna(); find indices
    nonempty_idx = df.index[df['processed_for_topics'].apply(lambda x: x and len(x)>0)].tolist()

    # initialize columns
    df['dominant_topic'] = None
    df['topic_keywords'] = None
    df['topic_score'] = None

    for i, idx in enumerate(nonempty_idx):
        tid, tscore = doc_topics[i]
        df.at[idx, 'dominant_topic'] = int(tid)
        df.at[idx, 'topic_keywords'] = topic_keywords.get(tid, "")
        df.at[idx, 'topic_score'] = float(tscore)

    # Save LDA model artifacts (optional)
    lda.save(os.path.join(OUT_DIR, "lda_model.model"))
    dictionary.save(os.path.join(OUT_DIR, "lda_dictionary.dict"))

    # OPTIONAL: save pyLDAvis html for interactive
    try:
        vis = gensimvis.prepare(lda, corpus, dictionary)
        pyLDAvis.save_html(vis, os.path.join(OUT_DIR, "lda_vis.html"))
    except Exception as e:
        print("pyLDAvis failed:", e)

# ----------------- SARCASTICITY DETECTION (Zero-shot / fine-tuned) -----------------
# We'll use Hugging Face pipelines. Two approaches:
# 1) Use a sarcasm-specific classifier (if you have a fine-tuned model)
# 2) Use zero-shot-classification (NLI) with labels ["sarcastic","not_sarcastic"]
#
# I'll implement zero-shot as a fallback because it's easy to run and doesn't require fine-tuned model.
#
# If you have a sarcasm model: set SARCASTIC_MODEL = "your/sarcasm-model" and use pipeline("text-classification", model=SARCASTIC_MODEL)

ZS_MODEL = "facebook/bart-large-mnli"  # zero-shot NLI model (default). Replace with sarcasm-specific model if available.
zero_shot = pipeline("zero-shot-classification", model=ZS_MODEL, device=0 if __import__('torch').cuda.is_available() else -1)

sar_labels = ["sarcastic", "not_sarcastic"]
def detect_sarcasm(text):
    if not text or str(text).strip()=="":
        return {"score": None, "label": None}
    try:
        res = zero_shot(text, candidate_labels=sar_labels, multi_label=False)
        # res: {labels:[...], scores:[...]}}
        # choose score for 'sarcastic'
        lab = res['labels'][0]
        score = float(res['scores'][0])
        # if top label is 'sarcastic' label => sarcasm score is score, else 1-score?
        if lab == 'sarcastic':
            return {"score": score, "label": "sarcastic" if score >= 0.5 else "maybe_sarcastic"}
        else:
            # not_sarcastic is top label
            # we can also inspect the second label if needed
            return {"score": 1.0 - score, "label": "not_sarcastic" if (1.0-score) >= 0.5 else "maybe_sarcastic"}
    except Exception as e:
        return {"score": None, "label": None}

# Apply sarcasm detection on the translated (English) text or cleaned text
sar_scores = []
sar_labels_out = []
for txt in df['translated'].astype(str).tolist():
    r = detect_sarcasm(txt)
    sar_scores.append(r.get('score'))
    sar_labels_out.append(r.get('label'))

df['sarcasm_score'] = sar_scores
df['sarcasm_label'] = sar_labels_out

# ----------------- HATE / OFFENSIVE SPEECH DETECTION -----------------
# Option A: Use an offensive/hate classifier such as "cardiffnlp/twitter-roberta-base-offensive" (recommended)
# Option B: Use zero-shot with labels: ["hate_speech","offensive","not_offensive"] but that's weaker.
#
# We'll try to use a lightweight pre-trained classifier if available; else fallback to zero-shot.

# You can change HATE_MODEL to a specific model you want to use:
HATE_MODEL = "cardiffnlp/twitter-roberta-base-offensive"  # recommended if available
hate_pipeline = None
try:
    hate_pipeline = pipeline("text-classification", model=HATE_MODEL, return_all_scores=True, device=0 if __import__('torch').cuda.is_available() else -1)
except Exception as e:
    print("Could not load the recommended hate model:", e)
    print("Falling back to zero-shot for hate detection")
    hate_pipeline = pipeline("zero-shot-classification", model=ZS_MODEL, device=0 if __import__('torch').cuda.is_available() else -1)

# If we have a text-classification model returning labels and scores, we'll map them.
hate_scores = []
hate_labels_out = []
for txt in df['translated'].astype(str).tolist():
    if not txt or txt.strip() == "":
        hate_scores.append(None); hate_labels_out.append(None); continue
    try:
        res = hate_pipeline(txt)
        # two possible pipeline outputs:
        # - when using text-classification with return_all_scores=True: res is list-of-lists dicts
        # - when zero-shot: dict with labels & scores
        if isinstance(res, dict) and 'labels' in res:  # zero-shot style
            # pick highest label and map to offensive/not
            lab = res['labels'][0]
            sc = float(res['scores'][0])
            hate_labels_out.append(lab)
            hate_scores.append(sc)
        elif isinstance(res, list) and len(res)>0 and isinstance(res[0], dict) and 'label' in res[0]:
            # huggingface returns a list of dicts each with label/score
            # If return_all_scores=True, res might be like: [[{'label':'OFF','score':0.6},...], ...]
            # Handle both nested list or single list cases:
            if isinstance(res[0], list):
                items = res[0]
            else:
                items = res
            # choose top by score
            top = max(items, key=lambda x: x.get('score', 0.0))
            hate_labels_out.append(top.get('label'))
            hate_scores.append(float(top.get('score', 0.0)))
        else:
            hate_labels_out.append(None)
            hate_scores.append(None)
    except Exception as e:
        hate_labels_out.append(None)
        hate_scores.append(None)

df['hate_score'] = hate_scores
df['hate_label'] = hate_labels_out

# ---------- Save enhanced dataframe ----------
df.to_csv(csv_path, index=False)
df.to_json(json_path, orient='records', force_ascii=False)
print("Saved with topics, sarcasm, hate detection:", csv_path, json_path)

# -------------------- VISUALIZATIONS for new attributes --------------------
import seaborn as sns
import matplotlib.pyplot as plt

# 1) Topics count
if 'dominant_topic' in df.columns and df['dominant_topic'].notnull().any():
    plt.figure(figsize=(8,5))
    sns.countplot(x=df['dominant_topic'].dropna().astype(int))
    plt.title("Document Count per Dominant Topic")
    plt.xlabel("Topic ID")
    plt.ylabel("Count")
    plt.tight_layout()
    plt.savefig(os.path.join(OUT_DIR, "topic_counts.png"))
    plt.close()

# 2) Sarcasm label distribution
if df['sarcasm_label'].notnull().any():
    plt.figure(figsize=(7,5))
    sns.countplot(x=df['sarcasm_label'].astype(str))
    plt.title("Sarcasm Label Distribution")
    plt.tight_layout()
    plt.savefig(os.path.join(OUT_DIR, "sarcasm_distribution.png"))
    plt.close()

# 3) Hate/offensive distribution (if labels exist)
if df['hate_label'].notnull().any():
    plt.figure(figsize=(7,5))
    sns.countplot(x=df['hate_label'].astype(str))
    plt.title("Hate / Offensive Label Distribution")
    plt.xticks(rotation=45)
    plt.tight_layout()
    plt.savefig(os.path.join(OUT_DIR, "hate_distribution.png"))
    plt.close()

# 4) Scatter: Sarcasm score vs Sentiment compound (are sarcastic memes more negative?)
plt.figure(figsize=(7,5))
sns.scatterplot(data=df, x='sarcasm_score', y='compound', hue='sent_label')
plt.title("Sarcasm score vs Sentiment (compound)")
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR, "sarcasm_vs_sentiment.png"))
plt.close()

# 5) Heatmap: topic vs average sentiment
if 'dominant_topic' in df.columns and df['dominant_topic'].notnull().any():
    topic_sent = df.groupby('dominant_topic')['compound'].mean().reset_index()
    plt.figure(figsize=(8,4))
    sns.barplot(data=topic_sent, x='dominant_topic', y='compound')
    plt.title("Average Sentiment by Dominant Topic")
    plt.tight_layout()
    plt.savefig(os.path.join(OUT_DIR, "topic_sentiment.png"))
    plt.close()

print("New plots saved to", OUT_DIR)

# -------------------- END: Topic Modeling + Sarcasm + Hate Detection --------------------

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 27.9/27.9 MB 35.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 94.1 MB/s eta 0:00:00


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

config.json: 0.00B [00:00, ?B/s]

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

model.safetensors:   0%|          | 0.00/1.63G [00:00<?, ?B/s]

...

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

Saved with topics, sarcasm, hate detection: /content/drive/MyDrive/reddit_political_memes/processed_results/meme_sentiment_results.csv /content/drive/MyDrive/reddit_political_memes/processed_results/meme_sentiment_results.json


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

New plots saved to /content/drive/MyDrive/reddit_political_memes/processed_results


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:

# Transformers for sarcasm/hate detection
from transformers import pipeline

# Define ROOT_DIR and OUT_DIR as they are needed for path construction
ROOT_DIR = "/content/drive/MyDrive/reddit_political_memes"
OUT_DIR = os.path.join(ROOT_DIR, "processed_results")
csv_path = os.path.join(OUT_DIR, 'meme_sentiment_results.csv')
json_path = os.path.join(OUT_DIR, 'meme_sentiment_results.json')

# ---------- PREPROCESS TEXT FOR TOPIC MODELLING ----------
def gensim_preprocess(text):
    # reuse earlier clean_text/tokenize if desired; gensim preprocessing for LDA:
    custom_filters = [lambda x: x.lower(), strip_punctuation, strip_numeric, remove_stopwords, strip_short]
    return preprocess_string(text or "", custom_filters)

# create a tokens column if not present (it is present in your script)
df['processed_for_topics'] = df['tokens'].apply(lambda t: t if isinstance(t, list) and len(t)>0 else gensim_preprocess(df.loc[df.index[df['tokens'] == t].tolist()[0],'cleaned']) if False else gensim_preprocess(df['cleaned'].iloc[0]) if False else gensim_preprocess(" ".join(t) if isinstance(t, list) else (t or "")))
# The above line is defensive but a little odd — simpler: if tokens present, join them, else run gensim_preprocess
# Let's correct more robustly:
def _ensure_tokens(row):
    if isinstance(row['tokens'], list) and len(row['tokens'])>0:
        return [w for w in row['tokens']]
    else:
        return gensim_preprocess(row['cleaned'] or "")
df['processed_for_topics'] = df.apply(_ensure_tokens, axis=1)

# Filter out empty documents
topic_docs = df['processed_for_topics'].apply(lambda x: x if x and len(x)>0 else None).dropna().tolist()

# create dictionary and corpus
dictionary = corpora.Dictionary(topic_docs)
# Filter extremes to remove very rare and very common tokens
dictionary.filter_extremes(no_below=3, no_above=0.5)  # tune these
corpus = [dictionary.doc2bow(doc) for doc in topic_docs]

if len(dictionary) == 0 or len(corpus) == 0:
    print("Not enough tokens for LDA. Skipping topic modelling.")
    df['dominant_topic'] = None
    df['topic_keywords'] = None
else:
    # ---------- LDA Model ----------
    NUM_TOPICS = 6  # tune (try 5-12)
    lda = models.LdaModel(corpus=corpus,
                          id2word=dictionary,
                          num_topics=NUM_TOPICS,
                          random_state=42,
                          passes=10,
                          alpha='auto',
                          per_word_topics=True)

    # map each doc in corpus back to row to assign dominant topic
    # build topic keywords
    topic_keywords = {}
    for tid in range(NUM_TOPICS):
        words_probs = lda.show_topic(tid, topn=8)
        topic_keywords[tid] = ", ".join([w for w,p in words_probs])

    # Get dominant topic per doc
    def get_doc_topic(bow):
        topics = lda.get_document_topics(bow)
        if not topics:
            return None, None
        topics = sorted(topics, key=lambda x: x[1], reverse=True)
        tid, score = topics[0]
        return int(tid), float(score)

    # Apply only to non-empty docs and then put back into df
    doc_topics = [get_doc_topic(b) for b in corpus]  # corresponds to topic_docs order
    # create a mapping from doc index in topic_docs -> df index
    # our topic_docs was built from df.dropna(); find indices
    nonempty_idx = df.index[df['processed_for_topics'].apply(lambda x: x and len(x)>0)].tolist()

    # initialize columns
    df['dominant_topic'] = None
    df['topic_keywords'] = None
    df['topic_score'] = None

    for i, idx in enumerate(nonempty_idx):
        tid, tscore = doc_topics[i]
        df.at[idx, 'dominant_topic'] = int(tid)
        df.at[idx, 'topic_keywords'] = topic_keywords.get(tid, "")
        df.at[idx, 'topic_score'] = float(tscore)

    # Save LDA model artifacts (optional)
    lda.save(os.path.join(OUT_DIR, "lda_model.model"))
    dictionary.save(os.path.join(OUT_DIR, "lda_dictionary.dict"))

    # OPTIONAL: save pyLDAvis html for interactive
    try:
        vis = gensimvis.prepare(lda, corpus, dictionary)
        pyLDAvis.save_html(vis, os.path.join(OUT_DIR, "lda_vis.html"))
    except Exception as e:
        print("pyLDAvis failed:", e)

# ----------------- SARCASTICITY DETECTION (Zero-shot / fine-tuned) -----------------
# We'll use Hugging Face pipelines. Two approaches:
# 1) Use a sarcasm-specific classifier (if you have a fine-tuned model)
# 2) Use zero-shot-classification (NLI) with labels ["sarcastic","not_sarcastic"]
#
# I'll implement zero-shot as a fallback because it's easy to run and doesn't require fine-tuned model.
#
# If you have a sarcasm model: set SARCASTIC_MODEL = "your/sarcasm-model" and use pipeline("text-classification", model=SARCASTIC_MODEL)

ZS_MODEL = "facebook/bart-large-mnli"  # zero-shot NLI model (default). Replace with sarcasm-specific model if available.
zero_shot = pipeline("zero-shot-classification", model=ZS_MODEL, device=0 if __import__('torch').cuda.is_available() else -1)

sar_labels = ["sarcastic", "not_sarcastic"]
def detect_sarcasm(text):
    if not text or str(text).strip()=="":
        return {"score": None, "label": None}
    try:
        res = zero_shot(text, candidate_labels=sar_labels, multi_label=False)
        # res: {labels:[...], scores:[...]}}
        # choose score for 'sarcastic'
        lab = res['labels'][0]
        score = float(res['scores'][0])
        # if top label is 'sarcastic' label => sarcasm score is score, else 1-score?
        if lab == 'sarcastic':
            return {"score": score, "label": "sarcastic" if score >= 0.5 else "maybe_sarcastic"}
        else:
            # not_sarcastic is top label
            # we can also inspect the second label if needed
            return {"score": 1.0 - score, "label": "not_sarcastic" if (1.0-score) >= 0.5 else "maybe_sarcastic"}
    except Exception as e:
        return {"score": None, "label": None}

# Apply sarcasm detection on the translated (English) text or cleaned text
sar_scores = []
sar_labels_out = []
for txt in df['translated'].astype(str).tolist():
    r = detect_sarcasm(txt)
    sar_scores.append(r.get('score'))
    sar_labels_out.append(r.get('label'))

df['sarcasm_score'] = sar_scores
df['sarcasm_label'] = sar_labels_out

# ----------------- HATE / OFFENSIVE SPEECH DETECTION -----------------
# Option A: Use an offensive/hate classifier such as "cardiffnlp/twitter-roberta-base-offensive" (recommended)
# Option B: Use zero-shot with labels: ["hate_speech","offensive","not_offensive"] but that's weaker.
#
# We'll try to use a lightweight pre-trained classifier if available; else fallback to zero-shot.

# You can change HATE_MODEL to a specific model you want to use:
HATE_MODEL = "cardiffnlp/twitter-roberta-base-offensive"  # recommended if available
hate_pipeline = None
try:
    hate_pipeline = pipeline("text-classification", model=HATE_MODEL, return_all_scores=True, device=0 if __import__('torch').cuda.is_available() else -1)
except Exception as e:
    print("Could not load the recommended hate model:", e)
    print("Falling back to zero-shot for hate detection")
    hate_pipeline = pipeline("zero-shot-classification", model=ZS_MODEL, device=0 if __import__('torch').cuda.is_available() else -1)

# If we have a text-classification model returning labels and scores, we'll map them.
hate_scores = []
hate_labels_out = []
for txt in df['translated'].astype(str).tolist():
    if not txt or txt.strip() == "":
        hate_scores.append(None); hate_labels_out.append(None); continue
    try:
        res = hate_pipeline(txt)
        # two possible pipeline outputs:
        # - when using text-classification with return_all_scores=True: res is list-of-lists dicts
        # - when zero-shot: dict with labels & scores
        if isinstance(res, dict) and 'labels' in res:  # zero-shot style
            # pick highest label and map to offensive/not
            lab = res['labels'][0]
            sc = float(res['scores'][0])
            hate_labels_out.append(lab)
            hate_scores.append(sc)
        elif isinstance(res, list) and len(res)>0 and isinstance(res[0], dict) and 'label' in res[0]:
            # huggingface returns a list of dicts each with label/score
            # If return_all_scores=True, res might be like: [[{'label':'OFF','score':0.6},...], ...]
            # Handle both nested list or single list cases:
            if isinstance(res[0], list):
                items = res[0]
            else:
                items = res
            # choose top by score
            top = max(items, key=lambda x: x.get('score', 0.0))
            hate_labels_out.append(top.get('label'))
            hate_scores.append(float(top.get('score', 0.0)))
        else:
            hate_labels_out.append(None)
            hate_scores.append(None)
    except Exception as e:
        hate_labels_out.append(None)
        hate_scores.append(None)

df['hate_score'] = hate_scores
df['hate_label'] = hate_labels_out

# ---------- Save enhanced dataframe ----------
df.to_csv(csv_path, index=False)
df.to_json(json_path, orient='records', force_ascii=False)
print("Saved with topics, sarcasm, hate detection:", csv_path, json_path)

# -------------------- VISUALIZATIONS for new attributes --------------------
import seaborn as sns
import matplotlib.pyplot as plt

# 1) Topics count
if 'dominant_topic' in df.columns and df['dominant_topic'].notnull().any():
    plt.figure(figsize=(8,5))
    sns.countplot(x=df['dominant_topic'].dropna().astype(int))
    plt.title("Document Count per Dominant Topic")
    plt.xlabel("Topic ID")
    plt.ylabel("Count")
    plt.tight_layout()
    plt.savefig(os.path.join(OUT_DIR, "topic_counts.png"))
    plt.close()

# 2) Sarcasm label distribution
if df['sarcasm_label'].notnull().any():
    plt.figure(figsize=(7,5))
    sns.countplot(x=df['sarcasm_label'].astype(str))
    plt.title("Sarcasm Label Distribution")
    plt.tight_layout()
    plt.savefig(os.path.join(OUT_DIR, "sarcasm_distribution.png"))
    plt.close()

# 3) Hate/offensive distribution (if labels exist)
if df['hate_label'].notnull().any():
    plt.figure(figsize=(7,5))
    sns.countplot(x=df['hate_label'].astype(str))
    plt.title("Hate / Offensive Label Distribution")
    plt.xticks(rotation=45)
    plt.tight_layout()
    plt.savefig(os.path.join(OUT_DIR, "hate_distribution.png"))
    plt.close()

# 4) Scatter: Sarcasm score vs Sentiment compound (are sarcastic memes more negative?)
plt.figure(figsize=(7,5))
sns.scatterplot(data=df, x='sarcasm_score', y='compound', hue='sent_label')
plt.title("Sarcasm score vs Sentiment (compound)")
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR, "sarcasm_vs_sentiment.png"))
plt.close()

# 5) Heatmap: topic vs average sentiment
if 'dominant_topic' in df.columns and df['dominant_topic'].notnull().any():
    topic_sent = df.groupby('dominant_topic')['compound'].mean().reset_index()
    plt.figure(figsize=(8,4))
    sns.barplot(data=topic_sent, x='dominant_topic', y='compound')
    plt.title("Average Sentiment by Dominant Topic")
    plt.tight_layout()
    plt.savefig(os.path.join(OUT_DIR, "topic_sentiment.png"))
    plt.close()

print("New plots saved to", OUT_DIR)

# -------------------- END: Topic Modeling + Sarcasm + Hate Detection --------------------

In [ ]:
import pandas as pd
import re
from datetime import datetime

csv_path = os.path.join(OUT_DIR, 'meme_sentiment_results.csv')
df = pd.read_csv(csv_path)

# try to extract date from filename patterns like 2024-03-12 or 20240312 or 12-03-2024
def extract_date_from_filename(fname):
    s = str(fname)
    # yyyy-mm-dd
    m = re.search(r'(20\d{2})[-_]?([01]\d)[-_]?([0-3]\d)', s)
    if m:
        try:
            return datetime.strptime("".join(m.groups()), "%Y%m%d")
        except:
            pass
    # dd-mm-yyyy
    m2 = re.search(r'([0-3]\d)[-_]([01]\d)[-_](20\d{2})', s)
    if m2:
        try:
            return datetime.strptime("".join(m2.groups()[::-1]), "%Y%m%d")
        except:
            pass
    return None

if 'date' not in df.columns:
    df['date'] = df['id'].apply(extract_date_from_filename)
df['date_parsed'] = pd.to_datetime(df['date'], errors='coerce')


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns

if df['date_parsed'].notnull().any():
    tmp = df.copy()
    tmp['week'] = tmp['date_parsed'].dt.to_period('W').astype(str)
    counts = tmp.groupby(['week','sent_label']).size().unstack(fill_value=0)
    frac = counts.divide(counts.sum(axis=1), axis=0)
    plt.figure(figsize=(12,5))
    frac[['positive','neutral','negative']].plot.area()
    plt.ylabel('Fraction')
    plt.title('Weekly sentiment share (stacked area)')
    plt.tight_layout()
    plt.savefig(os.path.join(OUT_DIR,'stacked_sentiment_share_weekly.png'))
    plt.close()


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
plt.figure(figsize=(12,6))
sub = df.groupby(['subreddit','sent_label']).size().unstack(fill_value=0)
sub_norm = sub.div(sub.sum(axis=1), axis=0).loc[sorted(sub.index)]
sub_norm[['positive','neutral','negative']].plot(kind='bar', stacked=True, figsize=(12,6))
plt.ylabel('Proportion')
plt.title('Normalized sentiment breakdown per subreddit')
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR,'subreddit_sentiment_stacked.png'))
plt.close()


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

<Figure size 1200x600 with 0 Axes>

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
plt.figure(figsize=(12,6))
sns.violinplot(data=df, x='subreddit', y='compound', order=sorted(df['subreddit'].unique()), inner=None)
sns.swarmplot(data=df, x='subreddit', y='compound', color='k', size=3, alpha=0.5)
plt.xticks(rotation=45)
plt.title('Sentiment score distribution by subreddit')
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR,'violin_sentiment_subreddit.png'))
plt.close()


Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replac

In [ ]:
from collections import Counter
pos_tokens = df[df['sent_label']=='positive']['tokens'].explode().dropna().astype(str).tolist()
neg_tokens = df[df['sent_label']=='negative']['tokens'].explode().dropna().astype(str).tolist()
pos_cnt = Counter(pos_tokens); neg_cnt = Counter(neg_tokens)
# top N words most different by normalized freq
def top_shift(n=25):
    all_words = set(list(pos_cnt.keys()) + list(neg_cnt.keys()))
    diffs = []
    for w in all_words:
        p = pos_cnt[w]/(sum(pos_cnt.values()) + 1e-9)
        q = neg_cnt[w]/(sum(neg_cnt.values()) + 1e-9)
        diffs.append((w, p-q))
    diffs_sorted = sorted(diffs, key=lambda x: x[1], reverse=True)[:n]
    return diffs_sorted
shift = top_shift(25)
shift_df = pd.DataFrame(shift, columns=['token','pos_minus_neg'])
plt.figure(figsize=(8,10))
sns.barplot(x='pos_minus_neg', y='token', data=shift_df)
plt.title('Top tokens more common in positive vs negative memes (positive -> top)')
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR,'word_shift_pos_vs_neg.png'))
plt.close()


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
from collections import Counter
import itertools
def top_ngrams(tokens_series, ngram=2, topk=30):
    all_bigrams=[]
    for t in tokens_series.dropna():
        if isinstance(t, str):
            toks = t.split()
        else:
            toks = t
        all_bigrams += list(zip(toks, toks[1:])) if len(toks)>1 else []
    bigrams = [' '.join(b) for b in all_bigrams]
    return Counter(bigrams).most_common(topk)

top_bigrams = top_ngrams(df['tokens'], ngram=2, topk=30)
bigram_df = pd.DataFrame(top_bigrams, columns=['bigram','freq'])
plt.figure(figsize=(8,10))
sns.barplot(x='freq', y='bigram', data=bigram_df)
plt.title('Top 30 bigrams')
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR,'top_bigrams_extra.png'))
plt.close()


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
import os
import pandas as pd
import json
from sklearn.feature_extraction.text import CountVectorizer
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

# Define ROOT_DIR and OUT_DIR (assuming they are set in a previous cell, but re-defining for clarity)
ROOT_DIR = "/content/drive/MyDrive/reddit_political_memes"
OUT_DIR = os.path.join(ROOT_DIR, "processed_results")
csv_path = os.path.join(OUT_DIR, 'meme_sentiment_results.csv')

# Load the DataFrame
df = pd.read_csv(csv_path)

# Function to parse string representation of list back to a list
def parse_tokens_from_string(s):
    try:
        # Safely evaluate if it's a string that looks like a list
        if isinstance(s, str) and s.startswith('[') and s.endswith(']'):
            # Use json.loads to convert string representation of list to actual list
            return json.loads(s.replace("'", '"'))
        return [] # Return empty list if not a parsable string representation of a list
    except (json.JSONDecodeError, AttributeError):
        return []

# Apply the parsing function to the 'tokens' column
df['tokens'] = df['tokens'].apply(parse_tokens_from_string)

# Convert lists of tokens to space-separated strings for CountVectorizer
# Handle cases where 'tokens' might be an empty list or not a list
tok_texts = df['tokens'].apply(lambda x: " ".join(x) if isinstance(x, list) else "")

cv = CountVectorizer(max_features=100)  # top 100 tokens
X = cv.fit_transform(tok_texts)
cooc = (X.T @ X).toarray()
labels = cv.get_feature_names_out()
cooc_df = pd.DataFrame(cooc, index=labels, columns=labels)
plt.figure(figsize=(12,10))
sns.heatmap(cooc_df, vmax=np.percentile(cooc,95), cmap='magma')
plt.title('Token co-occurrence heatmap (top 100 tokens)')
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR,'token_cooccurrence_heatmap.png'))
plt.close()

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer
tok_texts = df['tokens'].apply(lambda x: " ".join(x))
cv = CountVectorizer(max_features=100)  # top 100 tokens
X = cv.fit_transform(tok_texts)
cooc = (X.T @ X).toarray()
import numpy as np
labels = cv.get_feature_names_out()
cooc_df = pd.DataFrame(cooc, index=labels, columns=labels)
plt.figure(figsize=(12,10))
sns.heatmap(cooc_df, vmax=np.percentile(cooc,95), cmap='magma')
plt.title('Token co-occurrence heatmap (top 100 tokens)')
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR,'token_cooccurrence_heatmap.png'))
plt.close()


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
top_pos = df.sort_values('compound', ascending=False).head(10)
top_neg = df.sort_values('compound', ascending=True).head(10)
import shutil
os.makedirs(os.path.join(OUT_DIR,'examples/positive'), exist_ok=True)
os.makedirs(os.path.join(OUT_DIR,'examples/negative'), exist_ok=True)
for _, r in top_pos.iterrows():
    try: shutil.copy(r['filepath'], os.path.join(OUT_DIR,'examples/positive', os.path.basename(r['filepath'])))
    except: pass
for _, r in top_neg.iterrows():
    try: shutil.copy(r['filepath'], os.path.join(OUT_DIR,'examples/negative', os.path.basename(r['filepath'])))
    except: pass
print("Saved extreme meme examples to:", os.path.join(OUT_DIR,'examples'))


Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replac

Saved extreme meme examples to: /content/drive/MyDrive/reddit_political_memes/processed_results/examples


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# pip install sentence-transformers umap-learn
from sentence_transformers import SentenceTransformer
import umap

texts = df['translated'].fillna('').astype(str).tolist()
model = SentenceTransformer('all-MiniLM-L6-v2')  # fast
emb = model.encode(texts, show_progress_bar=True)
reducer = umap.UMAP(n_components=2, random_state=42)
emb2 = reducer.fit_transform(emb)
plt.figure(figsize=(10,8))
sns.scatterplot(x=emb2[:,0], y=emb2[:,1], hue=df['sent_label'], palette='viridis', alpha=0.8)
plt.title('UMAP of meme text embeddings (colored by sentiment)')
plt.legend()
plt.tight_layout()
plt.savefig(os.path.join(OUT_DIR,'umap_embeddings_sentiment.png'))
plt.close()


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

...

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

Batches:   0%|          | 0/18 [00:00<?, ?it/s]

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:203: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag